<h1>Settings</h1>

<h2>Database settings</h2>

In [1]:
%var vantageInstance               = "Transcend-Production-AWS"
    ,workingDatabase               = "ADLSLSEMEA_Scope3"
    ,georefPrefixe                 = "GEO_"
    ,foreignTablePrefixe           = "FT_"
    ,coreTablePrefixe              = "CORE_"
    ,optTablePrefixe               = "OPT_"
    ,splitSuffixe                  = "_SPLIT"
    ,authReadNOS                   = "GA_auth_read_nos"
    ,objectStoreInputDataBucketURL = "/gs/storage.googleapis.com/green-agenda/GeoRef/"

<h2>Entities</h2>

In [2]:
%var entityRef         = "Entity_ref"
    ,featureClassRef   = "Feature_class_ref"
    ,featureCodeRef    = "Feature_code_ref"
    ,countryRef        = "Country_ref"
    ,subregionRef      = "Subregion_ref"
    ,egridSubregionRef = "Egrid_subregion_ref"
    ,egrid2020Subregion = "EGRID2020_SUBREGIONS"

<h1>Connection to Vantage</h1>

In [3]:
%connect ${vantageInstance}

Success: 'Transcend-Production-AWS' connection established and activated for user 'gl186002'


<h1>Extension: Addition of a "default" value with geo_id = 0</h1>

In [4]:
delete from ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef} where geo_id = 0

Success: 1 rows affected

In [5]:
insert into ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef}
       (geo_id,geo_name ,geo_ascii_name,geo_feature_code_id,country_geo_id,population)
values (0     ,'Default','Default'     ,'N_ND'             ,0             ,0         )
;

Success: 1 rows affected

<h1>Extension: Manual addition of a Mexico and New Zealand entities</h1>

<p>Their batch integration had been rejected due to some unrecognized characters for alternate names</p>

In [4]:
delete from ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef} where geo_id in (2186224,3996063);

Success: 0 rows affected

In [5]:
insert into ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef}
       (geo_id ,geo_name  ,geo_ascii_name,geo_latitude,geo_longitude,geo_feature_code_id,country_geo_id,population)
values (3996063,'Mexico'  ,'Mexico'      ,23          ,-102         ,'PCLI'             ,3996063       ,126190788 )
;
insert into ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef}
       (geo_id ,geo_name     ,geo_ascii_name,geo_latitude,geo_longitude,geo_feature_code_id,country_geo_id,population)
values (2186224,'New Zealand','New Zealand' ,-42         ,174          ,'PCLI'             ,2186224       ,4885500   )
;

Success: 1 rows affected

Success: 1 rows affected

<h1>Extension: Addition of an extension record type for feature_class (feature_class_id = 'E') and feature_code (feature_code_id = 'ESR') tables</h1>

In [35]:
delete from ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${featureClassRef} where geo_feature_class_id = 'E'

Success: 0 rows affected

In [36]:
insert into ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${featureClassRef}
       (geo_feature_class_id,geo_feature_class_desc            )
values ('E'                 ,'Extension to the original source')
;

Success: 1 rows affected

In [38]:
delete from ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${featureCodeRef} where geo_feature_code_id = 'ESR'

Success: 0 rows affected

In [39]:
insert into ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${featureCodeRef}
       (geo_feature_code_id,geo_feature_class_id,geo_feature_code_name,geo_feature_code_desc                                         )
values ('ESR'              ,'E'                 ,'subregion extension','a subregion that is an extension to the original data source')
;

Success: 1 rows affected

<h1>Extension: Addition of Subregions data</h1>

<h2>Creation of "Subregion_ref" table</h2>

In [4]:
drop table ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef};

Success: 34 rows affected

In [5]:
create table ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}
(geo_id                   integer
,protocol_id              varchar(10)
,subregion_id             char(4)
,subregion_shape_length   float
,subregion_shape_area     float
,subregion_shape_geometry sysudtlib.st_geometry(16776192) inline length 9920
)
unique primary index (geo_id)
index (subregion_shape_geometry)
;

Success: 0 rows affected

<h2> Creation of eGrid (US EPA) foreign and staging tables </h2>

<h3> Foreign Table: list of eGrid subregions list </h3>

In [42]:
drop table ${workingDatabase}.${georefPrefixe}${foreignTablePrefixe}${egridSubregionRef};

Success: 29 rows affected

In [43]:
create foreign table ${workingDatabase}.${georefPrefixe}${foreignTablePrefixe}${egridSubregionRef}
 ,external security invoker trusted ${authReadNOS}
  using(location('${objectStoreInputDataBucketURL}GEO_Subregion_ref/Egrid_subregion_ref/'))
;

Success: 0 rows affected

WARNING: [Teradata Database] [Warning 4968] Unsupported record_delimiter:'
'. Table Created: with record_delimiter value:'\n'.Use READ_NOS RAW mode to determine the delimiters.

In [44]:
select top 10 * from ${workingDatabase}.${georefPrefixe}${foreignTablePrefixe}${egridSubregionRef};

Location subregion_id geo_name 1 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv NYLI NPCC Long Island  2 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv RFCE RFC East  3 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv SRVC SERC Virginia/Carolina 4 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv SRTV SERC Tennessee Valley  5 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv SRSO SERC South  6 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv FRCC FRCC All  7 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv SRMV SERC Mississippi Valley  8 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv NYUP NPCC Upstate NY  9 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv NYCW NPCC NYC/Westchester  10 /GS/storage.googleapis.com/green-agenda/GeoRef/GEO_Subregion_ref/Egrid_subregion_ref/Egrid_subregion_ref.csv NEWE NPCC New England

<h3> Staging Table: eGrid 2020 subregions </h3>

This table was loaded using the TDGeoImport. Source: https://docs.teradata.com/r/Teradata-Geospatial-Utilities-User-Guide/June-2022
<p><b><i>
java -Xms256m -Xmx512m -classpath .;"C:\Program Files\Teradata\Client\16.20\Teradata Parallel Transporter\tptwizard\jars\*";"C:\Program Files\Teradata\Client\16.20\bin\tdgeospatial.jar"; com.teradata.geo.TDGeoImport -logmech ldap -l tdprd2.td.teradata.com/gl186002,xxxxx -s ADLSLSEMEA_Scope3 -f "C:\temp\TdGeoImportExport\egrid2020_subregions\eGRID2020_subregions.shp"
</i></b></p>


In [13]:
/* DDL of the table:
CREATE SET TABLE ADLSLSEMEA_Scope3.EGRID2020_SUBREGIONS ,FALLBACK ,
     NO BEFORE JOURNAL,
     NO AFTER JOURNAL,
     CHECKSUM = DEFAULT,
     DEFAULT MERGEBLOCKRATIO,
     MAP = TD_MAP1
     (
      ZIPSUBREGI VARCHAR(254) CHARACTER SET LATIN NOT CASESPECIFIC,
      SHAPE_LENG FLOAT,
      SHAPE_LE_1 FLOAT,
      SHAPE_AREA FLOAT,
      GEOM SYSUDTLIB.ST_GEOMETRY(16776192) INLINE LENGTH 9920)
PRIMARY INDEX ( ZIPSUBREGI );
*/

Success: 0 rows affected

In [19]:
select zipsubregi
      ,shape_leng
      ,shape_le_1
      ,shape_area
--    ,geom
from   ${workingDatabase}.${egrid2020Subregion};

ZIPSUBREGI SHAPE_LENG SHAPE_LE_1 SHAPE_AREA 1 MROE 74.3660885611 74.3660885611 9.75179474945 2 RMPA 81.1251230058 81.1251230058 53.0405301217 3 SRMW 77.1370567493 77.1370567493 27.8865748607 4 RFCW 157.673576629 157.673576629 40.912294937 5 SPNO 54.2900419782 54.2900419782 25.4986345177 6 AZNM 85.34681275 85.34681275 54.9911752776 7 RFCM 37.0551054603 37.0551054603 11.7732049478 8 NYCW 9.7302159455 9.7302159455 0.201027741835 9 NYLI 22.8807889703 22.8807889703 0.328408836326 10 NEWE 107.279555661 107.279555661 19.1818891497 11 FRCC 147.119699168 147.119699168 12.2799774877 12 RFCE 109.18765479 109.18765479 16.1856602275 13 SRSO 92.7375720282 92.7375720282 29.9297724294 14 PRMS 0 11.6275631217 0.762386723703 15 HIOA 3.85947580396 3.85947580396 0.135622052088 16 MROW 118.469796775 118.469796775 109.918613049 17 SRMV 210.998694103 210.998694103 29.8526080914 18 NYUP 28.9152058526 28.9152058526 13.3986252771 19 SRTV 77.8521477346 77.8521477346 27.2529926717 20 SRVC 118.068242267 118.068242267 26.8363219822 21 SPSO 122.531213065 122.531213065 37.7515139697 22 CAMX 75.5674655411 75.5674655411 35.7887219808 23 NWPP 207.631376993 207.631376993 186.094936955 24 AKMS 804.533840705 804.533840705 243.100970876 25 AKGD 122.099468561 122.099468561 36.7146429238 26 HIMS 15.3870777895 15.3870777895 1.3046099209 27 ERCT 147.354169139 147.354169139 49.8258260459

<h2> Insertion to the final tables </h2>

In [49]:
delete from ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef}
where  geo_id in (select  -hashbucket(hashrow(zipsubregi))
                  from    ${workingDatabase}.${egrid2020Subregion}
                 )
;

Success: 0 rows affected

In [52]:
insert into ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef}
select  -hashbucket(hashrow(egrid2020.zipsubregi)) as geo_id
       ,subregion_ref.geo_name                     as geo_name
       ,subregion_ref.geo_name                     as geo_ascii_name
       ,egrid2020.geom.ST_PointOnSurface().st_y()  as geo_latitude
       ,egrid2020.geom.ST_PointOnSurface().st_x()  as geo_longitude
       ,'ESR'                                      as geo_feature_code_id
       ,geo_us.geo_id                              as country_geo_id
       ,null                                       as admin_lv1_geo_id
       ,null                                       as admin_lv2_geo_id
       ,0                                          as population
       ,null                                       as timezone_id
from    ${workingDatabase}.${egrid2020Subregion} egrid2020
inner join
        ${workingDatabase}.${georefPrefixe}${foreignTablePrefixe}${egridSubregionRef} subregion_ref
on      egrid2020.zipsubregi = subregion_ref.subregion_id
cross join
       (select  geo_id
        from    ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${countryRef}
        where   country_code_iso = 'US'
       ) geo_us
;

Success: 27 rows affected

WARNING: [Teradata Database] [Warning 4375] Files/records in foreign table(s) were skipped.

In [53]:
select  *
from    ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef}
where   geo_id in (select  -hashbucket(hashrow(zipsubregi))
                  from    ${workingDatabase}.${egrid2020Subregion}
                 )
;

geo_id geo_name geo_ascii_name geo_latitude geo_longitude geo_feature_code_id country_geo_id admin_lv1_geo_id admin_lv2_geo_id population timezone_id 1 -887881 ASCC Miscellaneous  ASCC Miscellaneous  51.25855300 -179.10509431 ESR 6252001 0 2 -543066 WECC Rockies  WECC Rockies  43.70522750 -105.53781539 ESR 6252001 0 3 -257169 NPCC New England  NPCC New England  40.98260800 -73.62726759 ESR 6252001 0 4 -565583 MRO East  MRO East  43.74108050 -87.79411826 ESR 6252001 0 5 -376303 ERCOT All  ERCOT All  26.00148300 -97.19848937 ESR 6252001 0 6 -816636 SPP South  SPP South  29.42721150 -91.33078903 ESR 6252001 0 7 -411952 HICC Miscellaneous  HICC Miscellaneous  19.18130350 -155.90915556 ESR 6252001 0 8 -554793 Puerto Rico Miscellaneous Puerto Rico Miscellaneous 17.88251751 -66.53219716 ESR 6252001 0 9 -120813 RFC Michigan  RFC Michigan  41.74337600 -83.43645476 ESR 6252001 0 10 -685886 NPCC Upstate NY  NPCC Upstate NY  41.26363850 -73.92836593 ESR 6252001 0 11 -218049 RFC West  RFC West  36.53656750 -82.64360539 ESR 6252001 0 12 -169874 SERC Mississippi Valley  SERC Mississippi Valley  28.92084300 -89.41409580 ESR 6252001 0 13 -184433 ASCC Alaska Grid  ASCC Alaska Grid  59.11368600 -151.68134734 ESR 6252001 0 14 -234506 HICC Oahu  HICC Oahu  21.29091650 -157.71681121 ESR 6252001 0 15 -673125 SPP North  SPP North  36.75875760 -93.94732218 ESR 6252001 0 16 -844199 RFC East  RFC East  37.03541300 -76.07790823 ESR 6252001 0 17 -540774 WECC Southwest  WECC Southwest  33.30907500 -104.35633779 ESR 6252001 0 18 -624687 SERC Tennessee Valley  SERC Tennessee Valley  33.76929370 -90.15907819 ESR 6252001 0 19 -597610 WECC California  WECC California  32.66995430 -117.15670230 ESR 6252001 0 20 -694706 NPCC Long Island  NPCC Long Island  40.58951550 -73.63107712 ESR 6252001 0 21 -125629 SERC South  SERC South  29.98076650 -85.49442822 ESR 6252001 0 22 -1000882 WECC Northwest  WECC Northwest  35.46835950 -108.44326944 ESR 6252001 0 23 -988009 MRO West  MRO West  40.48453750 -91.44099360 ESR 6252001 0 24 -680562 FRCC All  FRCC All  24.52304700 -81.96418373 ESR 6252001 0 25 -34460 SERC Midwest  SERC Midwest  34.85199475 -95.57860006 ESR 6252001 0 26 -195971 NPCC NYC/Westchester  NPCC NYC/Westchester  40.56600110 -74.05013018 ESR 6252001 0 27 -375118 SERC Virginia/Carolina SERC Virginia/Carolina 32.07832050 -80.88042239 ESR 6252001 0

In [54]:
delete from ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}
where  geo_id in (select  -hashbucket(hashrow(zipsubregi))
                  from    ${workingDatabase}.${egrid2020Subregion}
                 )
;

Success: 0 rows affected

In [6]:
insert into ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}
select  -hashbucket(hashrow(zipsubregi)) as geo_id
       ,'EGRID2020'                      as protocol_id
       ,zipsubregi                       as subregion_id
       ,shape_le_1                       as subregion_shape_length
       ,shape_area                       as subregion_shape_area
       ,geom                             as subregion_shape_geometry
from    ${workingDatabase}.${egrid2020Subregion}
;

Success: 27 rows affected

In [7]:
select geo_id
      ,protocol_id
      ,subregion_id
      ,subregion_shape_length
      ,subregion_shape_area
--    ,subregion_shape_geometry
from   ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}
;

geo_id protocol_id subregion_id subregion_shape_length subregion_shape_area 1 -887881 EGRID2020 AKMS 804.533840705 243.100970876 2 -543066 EGRID2020 RMPA 81.1251230058 53.0405301217 3 -257169 EGRID2020 NEWE 107.279555661 19.1818891497 4 -565583 EGRID2020 MROE 74.3660885611 9.75179474945 5 -376303 EGRID2020 ERCT 147.354169139 49.8258260459 6 -816636 EGRID2020 SPSO 122.531213065 37.7515139697 7 -411952 EGRID2020 HIMS 15.3870777895 1.3046099209 8 -554793 EGRID2020 PRMS 11.6275631217 0.762386723703 9 -120813 EGRID2020 RFCM 37.0551054603 11.7732049478 10 -685886 EGRID2020 NYUP 28.9152058526 13.3986252771 11 -218049 EGRID2020 RFCW 157.673576629 40.912294937 12 -169874 EGRID2020 SRMV 210.998694103 29.8526080914 13 -184433 EGRID2020 AKGD 122.099468561 36.7146429238 14 -234506 EGRID2020 HIOA 3.85947580396 0.135622052088 15 -673125 EGRID2020 SPNO 54.2900419782 25.4986345177 16 -844199 EGRID2020 RFCE 109.18765479 16.1856602275 17 -540774 EGRID2020 AZNM 85.34681275 54.9911752776 18 -624687 EGRID2020 SRTV 77.8521477346 27.2529926717 19 -597610 EGRID2020 CAMX 75.5674655411 35.7887219808 20 -694706 EGRID2020 NYLI 22.8807889703 0.328408836326 21 -125629 EGRID2020 SRSO 92.7375720282 29.9297724294 22 -1000882 EGRID2020 NWPP 207.631376993 186.094936955 23 -988009 EGRID2020 MROW 118.469796775 109.918613049 24 -680562 EGRID2020 FRCC 147.119699168 12.2799774877 25 -34460 EGRID2020 SRMW 77.1370567493 27.8865748607 26 -195971 EGRID2020 NYCW 9.7302159455 0.201027741835 27 -375118 EGRID2020 SRVC 118.068242267 26.8363219822

<h2>Creation of a subregion table with polygon splits into smaller parts</h2>

<p>Subregions are defined by complex multipolygons. Determining if a geometry point is contained in one of these multipolygons is done by a cross join and a CPU intensive operation.</p>
<p>The below table splits the complex multipolygons into smaller ones so that the joins are less skewed and less CPU intensive</p>
<p>Generation of subpolygons table takes approximately 30 minutes, mainly due to the high skew (only 27 rows)</p>

In [5]:
drop table ${workingDatabase}.${georefPrefixe}${optTablePrefixe}${subregionRef}${splitSuffixe};

ERROR: Unable to run SQL: Unable to run SQL query: Database reported error:3807:Object 'ADLSLSEMEA_Scope3.GEO_OPT_Subregion_ref_SPLIT' does not exist.

In [6]:
create table ${workingDatabase}.${georefPrefixe}${optTablePrefixe}${subregionRef}${splitSuffixe} as
(select poly_id     as geo_id
       ,sub_poly_id as subregion_split_id
       ,1           as flag_split
       ,split_geom  as subregion_shape_geometry_split
from    PolygonSplit(on (select  geo_id                   as geo_id
                                ,subregion_shape_geometry as subregion_shape_geometry
                                ,cast(10000 as integer)   as max_vertices
                         from    ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}
                         where   subregion_shape_geometry.ST_IsValid() = 1
                        )
                    ) subregion_split
union all
select  geo_id as geo_id
       ,0      as subregion_split_id
       ,0      as flag_split
       ,subregion_shape_geometry as subregion_shape_geometry_split
from    ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}
where   subregion_shape_geometry.ST_IsValid() = 0
)
with data
unique primary index(geo_id,subregion_split_id)
;

Success: 0 rows affected

In [9]:
select top 10 * from ${workingDatabase}.${georefPrefixe}${optTablePrefixe}${subregionRef}${splitSuffixe}

geo_id subregion_split_id flag_split subregion_shape_geometry_split 1 -844199 61 1 MULTIPOLYGON (((-77.219657000270303 38.342752825332695,-77.219657000270303 38.608982207541203,-77.214902999573724 38.61171800018559,-77.203981999569578 38.618146999884175,-77.203260999595443 38.618007999769418,-77.202687000104959 38.617758999977923,-77.201883999946574 38.617649000301185,-77.201487999671428 38.617899000138777,-77.20128400015642 38.618237000437261,-77.200698000112595 38.618456999790737,-77.200290000183315 38.618805999697202,-77.199645000116618 38.61912299992656,-77.199065000349435 38.619273999695395,-77.198402000352019 38.619364000248481,-77.19781500026204 38.619423000271297,-77.197076000357072 38.619463000317239,-77.196246999899074 38.619483000340267,-77.195061000065039 38.619538000178636,-77.194116999699759 38.619458000086695,-77.193352000394441 38.61944799962555,-77.192625000143607 38.619399000063879,-77.19224199956858 38.619249000341142,-77.191833999639357 38.619138999765084,-77.191208999595631 38.619258999902968,-77.190761999666506 38.619428999648676,-77.190290000383186 38.619647999855374,-77.189907999854256 38.61997699973881,-77.189728999693557 38.620285999599275,-77.189358999718024 38.620615000382031,-77.188938000088569 38.62064399992073,-77.188389999998435 38.620713999551469,-77.187624999793854 38.620923000196342,-77.186846999889099 38.621123000426167,-77.186080999638364 38.621372000217661,-77.185404999940772 38.621481999894456,-77.184818999896891 38.621571000401389,-77.18406600024565 38.621571000401389,-77.183250000387147 38.62165099959401,-77.182261999791422 38.621806000446611,-77.18019199966102 38.622883999796784,-77.176952000434426 38.623761999816509,-77.174902000326995 38.624218000160624,-77.16267500035093 38.627148000379975,-77.162615000282017 38.627162000126248,-77.160350000152334 38.627704999985838,-77.147548999786466 38.630771000181539,-77.13650100022096 38.633417999940775,-77.130201000175987 38.635017999980789,-77.132881999704466 38.641175999772599,-77.132815000212076 38.641739999701258,-77.132841999658524 38.642231999906926,-77.13307000028027 38.642660999905274,-77.133015999588679 38.643173000133913,-77.132949000096232 38.64367499990135,-77.132735000120135 38.643916000223271,-77.132681000327864 38.644156999645872,-77.132827999912251 38.644387000359814,-77.136082999830535 38.648721999720578,-77.136136999622806 38.649170999741898,-77.136310999552961 38.649621999855469,-77.136163999968574 38.649842000108265,-77.136337999898728 38.650259999599371,-77.13420100027588 38.662116999599903,-77.132501500144087 38.67371669996578,-77.132473999775243 38.673779899822591,-77.132427199955259 38.673845900168203,-77.130134999830318 38.675856000054409,-77.127905999562188 38.677740999747414,-77.126049000261105 38.679819000246709,-77.124563000082333 38.681753000400704,-77.12351100013251 38.68329899974907,-77.123400999556452 38.684115999653727,-77.122000999746319 38.685815999808597,-77.121100999611429 38.686615999828575,-77.11677299967414 38.689519999748256,-77.104809000135219 38.6970829995808,-77.10445800013656 38.697193000156858,-77.10419899988392 38.69730399987975,-77.104064999999707 38.697395999625712,-77.103922999746601 38.697506000201827,-77.103805999747067 38.697655999924507,-77.103705999632155 38.697753999947167,-77.103564000278368 38.697819000246739,-77.103305000025671 38.697884999693031,-77.102837000027478 38.697992000130739,-77.102202000421926 38.698105999991981,-77.101902000077189 38.698126000014952,-77.101683999916645 38.698118999692156,-77.10155900044748 38.698066999992136,-77.101157999941734 38.698048000015262,-77.100816000358066 38.69813200029165,-77.100514999967231 38.698216999714816,-77.099972000107698 38.698372999714195,-77.098667000181877 38.698807999989242,-77.097100999911163 38.699739999801182,-77.096051000053592 38.700542999959509,-77.095919000261631 38.700638999889975,-77.095693999778234 38.70080999968178,-77.095313000194778 38.701126999911196,-77.095142000402973 38.701301999887448,-77.09492200015012 38.7014969

+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++
<h2>Work in progress below - not to be considered in the short term</h2>
<h2>Creation of a manual Tesselation index for subregions</h2>

<p>Subregions are defined by complex multipolygons. Determining if a geometry point is contained in one of these multipolygons is done by a cross join and a CPU intensive operation.</p>
<p>Tesselation indexes by Teradata use MBRs (Minimum Bounding Rectangles). However, as subregions are complex forms, their MBR is too large to efficiently optimize a join.</p>
<p>As an alternative, we propose to create a tesselation grid based on integer longitude and latitude points : we divide the full referential into 64,800 rectangles identified by a <b>tesselation_id</b>. To determine the tesselation id of a geospatial point, we take the integer part of its latitude and longitude. We add 90 to the latitude and 180 to the longitude so that the range of values is always a positive integer. We then multiply the latidude+90 by 1000 and add the longitude+180 value, providing a unique tesselation_id for each of the 64,800 existing rectangles.</p>
<p>In the following materialized index, we determine which of these rectangles are contained (partially or totally) in every defined subregion.</p>

In [13]:
/*drop table ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}_TessIdx;*/

Success: 0 rows affected

In [11]:
/*
create table ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}_TessIdx as (
select  esr_shape_ref.geo_id
       ,tesselation_grid.tesselation_id
from    ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef} esr_shape_ref
inner join
       (select  cast(geo_longitude as integer)                 as longint
               ,cast(geo_latitude  as integer)                 as latint
               ,  cast(geo_latitude  +  90 as integer) * 1000
                + cast(geo_longitude + 180 as integer)         as tesselation_id
               ,new ST_Geometry('ST_Point',longint-1,latint-1) as geo_point1
               ,new ST_Geometry('ST_Point',longint+1,latint-1) as geo_point2
               ,new ST_Geometry('ST_Point',longint-1,latint+1) as geo_point3
               ,new ST_Geometry('ST_Point',longint+1,latint+1) as geo_point4
        from    ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef}
        group by 1,2,3,4
       ) tesselation_grid
on      esr_shape_ref.subregion_shape_geometry.ST_Contains(tesselation_grid.geo_point1) = 1
or      esr_shape_ref.subregion_shape_geometry.ST_Contains(tesselation_grid.geo_point2) = 1
or      esr_shape_ref.subregion_shape_geometry.ST_Contains(tesselation_grid.geo_point3) = 1
or      esr_shape_ref.subregion_shape_geometry.ST_Contains(tesselation_grid.geo_point4) = 1
where   esr_shape_ref.subregion_shape_area > 10
union all
select  esr_shape_ref.geo_id
       ,tesselation_grid.tesselation_id
from    ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef} esr_shape_ref
inner join
       (select    cast(geo_latitude  +  90 as integer) * 1000
                + cast(geo_longitude + 180 as integer)                 as tesselation_id
               ,new ST_Geometry('ST_Point',geo_longitude,geo_latitude) as geo_point
        from    ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${entityRef}
        group by 1,2
       ) tesselation_grid
on      esr_shape_ref.subregion_shape_geometry.ST_Contains(tesselation_grid.geo_point) = 1
where   esr_shape_ref.subregion_shape_area < 10
)
with data
primary index(tesselation_id)
unique index(geo_id,tesselation_id)
;
*/

Success: 0 rows affected

In [12]:
/*
select geo_id,count(*)
from ${workingDatabase}.${georefPrefixe}${coreTablePrefixe}${subregionRef}_TessIdx
group by 1
order by 1
;
*/

Success: 0 rows affected